In [134]:
import tensorflow as tf
import matplotlib.pyplot as plt
import numpy as np
from numpy.linalg import eig
import pandas as pd
from minisom import MiniSom  
import math
import ipynb
from sklearn.metrics import classification_report
import cv2
from itertools import chain

%matplotlib inline

### Import custom functions

In [135]:
# Import custom functions from seperate workbook
from ipynb.fs.full.helper_functions import *

Here we will implemente our deep SOM. The purpose here is to have a DSOM running, classifying some images, then being evaluated. 

### Data Preperation

In [136]:
# Read in our data
(x_train, y_train), (x_test, y_test) = tf.keras.datasets.mnist.load_data()

In [137]:
# Here we have to flatten our data so we are able to feed it to the SOM
x_test_r = flatten_and_reshape(x_test)
x_train_r = flatten_and_reshape(x_train)

### Create DSOM

Step 1: select area of image you are creating the som for.\
Step 2: train a SOM on that area of the image\
Step 3: add the index of that trained som and the data to an array\
Step 4: extract the winning node for each of the SOMs and their respective trained data section.\
Step 5: train a som based off these winning nodes

In [5]:
# This function will take our image and stride accross it based on the paramaters we have given it. 

# define the kernal size and the stride. 
# x_test.shape
# x_test_r.shape

# What we need to do here. We need to update teh convolve function to include the som dimensions we want to pass our 
# som. We also need to update the loop section to make sure we're applying the som correctly. I also want to make 
# sure the way we're saving out our SOM details is correct.


def apply_som_layer(image, kernel, som_y_size):
    # grab the spatial dimensions of the image, along with
    # the spatial dimensions of the kernel
    (iH, iW) = image.shape[:2]
    (kH, kW) = kernel.shape[:2]
    # allocate memory for the output image, taking care to
    # "pad" the borders of the input image so the spatial
    # size (i.e., width and height) are not reduced
    pad = (kW - 1) // 2
    image = cv2.copyMakeBorder(image, pad, pad, pad, pad, cv2.BORDER_REPLICATE)
    output = np.zeros((iH, iW), dtype="float32")
    # loop over the input image, "sliding" the kernel across
    # each (x, y)-coordinate from left-to-right and top to
    # bottom
    for y in np.arange(pad, iH + pad):
        for x in np.arange(pad, iW + pad):
            # extract the Region Of Interest of the image by extracting the
            # *center* region of the current (x, y)-coordinates
            # dimensions
            roi = image[y - pad:y + pad + 1, x - pad:x + pad + 1]
            # Now we flatten the ROI so we can pass it to our som function
            flat_roi = flatten_and_reshape(roi)            
            # now we're going to apply the SOM function to the given region of interest.
            som = create_train_som(flat_roi, som_y_size)
            # Now we extract thhe position of the winning SOM
            winning_pos = som.winner(flat_roi)
            # We now convert this coordinant into a numerical value so we can feed it to our next layer
            k = convert_coordinants(winning_pos, som_y_size)
            # store the convolved value in the output (x,y)-
            # coordinate of the output image
            output[y - pad, x - pad] = k
            
    # rescale the output image to be in the range [0, 255]
#     output = rescale_intensity(output, in_range=(0, 255))
#     output = (output * 255).astype("uint8")
    # return the output image
    return output



# https://www.pyimagesearch.com/2016/07/25/convolutions-with-opencv-and-python

In [138]:
kernel = np.array((
    [1, 1, 1, 1, 1],
    [1, 1, 1, 1, 1],
    [1, 1, 1, 1, 1],
    [1, 1, 1, 1, 1],
    [1, 1, 1, 1, 1]), dtype="int")

In [7]:
their_image = cv2.imread("/Users/morleypemberton/Documents/UNI/Semester 1 2022/DATA5709 Capstone B/testing_image/3d_pokemon.jpeg")
gray = cv2.cvtColor(their_image, cv2.COLOR_BGR2GRAY)

In [139]:
my_image = x_train[1]

In [140]:
kernel.shape

(5, 5)

In [25]:
print(gray.shape)
print(my_image.shape)
print(my_image)

(600, 800)
(28, 28)
[[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0  51 159 253
  159  50   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0  48 238 252 252
  252 237   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0  54 227 253 252 239
  233 252  57   6   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0  10  60 224 252 253 252 202
   84 252 253 122   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   

In [172]:
# image= my_image

# Here we get the shape of the image and the kernal. We use this so we can set how
# the kernal slides across the image
(iH, iW) = image.shape[:2]
(kH, kW) = kernel.shape[:2]

# Here we add a buffer to thhe entire image so that when we get to the boarder we dont 
# lose any of the image
pad = (kW - 1)

print(kW)

som_n_features = kernel.shape[1] * kernel.shape[0]
som_nurons = int((math.sqrt(5*math.sqrt(som_n_features))))

output = np.zeros((iH, iW), dtype="float32")

image = cv2.copyMakeBorder(my_image, pad, pad, pad, pad, cv2.BORDER_REPLICATE)
# print(image[1:100])

print(image.shape)

for y in np.arange(pad, iH + pad):
    # This second for loop allows us to slide across the "columns" or te elements in that 
    # sepcific array 
    for x in np.arange(pad, iW + pad):
        # Now that we haxxve the specific coordinants we're looking at on the image 
        # the height and width position (x,y) we can add the padding to get our patch
        roi = image[y - pad:y + pad + 1, x - pad:x + pad + 1]
        # Now, normally we would apply the kernal to our patch to augment the overall image
        # however we do not wish to do that. We are aiming to apply a SOM to this specific 
        # region of the image. 
#         print(roi)

5
(36, 36)


In [173]:
image= my_image

# Here we get the shape of the image and the kernal. We use this so we can set how
# the kernal slides across the image
(iH, iW) = image.shape[:2]
(kH, kW) = kernel.shape[:2]

# Here we add a buffer to thhe entire image so that when we get to the boarder we dont 
# lose any of the image
print(kW)
pad = (kW - 1) // 2

som_n_features = kernel.shape[1] * kernel.shape[0]
som_nurons = int((math.sqrt(5*math.sqrt(som_n_features))))

# output = np.zeros((iH, iW), dtype="float32")
output = []
image = cv2.copyMakeBorder(image, pad, pad, pad, pad, cv2.BORDER_REPLICATE)
image
print(kernel)
print(pad)
# Here we actually slide the kernal across. The first for loop allows us to slide across
# the height or each row as you will of the image, by the padding widthh
for y in np.arange(pad, iH + pad):
    # This second for loop allows us to slide across the "columns" or te elements in that 
    # sepcific array 
    for x in np.arange(pad, iW + pad):
        # Now that we have the specific coordinants we're looking at on the image 
        # the height and width position (x,y) we can add the padding to get our patch
        roi = image[y - pad:y + pad + 1, x - pad:x + pad + 1]
        # Now, normally we would apply the kernal to our patch to augment the overall image
        # however we do not wish to do that. We are aiming to apply a SOM to this specific 
        # region of the image. 
#         print(roi)
        # Ok so we train a SOM on the data. Then extract the winning SOM? Yep. 
        # Thats what we return because thats what we're going to use in our next level.
        res = [np.reshape(roi, (roi.shape[0]*roi.shape[1]))]
#         print(res.shape)
        # Firstly we must flatten the patch so we can pass it to our function
        # flattened_roi = flatten_and_reshape(roi)
        # now we're going to apply the SOM function to the given region of interest.
#         som = create_train_som(res,som_n_features)
        # Now we extract thhe position of the winning SOM
#         winning_pos = som.winner(res)
        # We now convert this coordinant into a numerical value so we can feed it to our next layer
#         k = convert_coordinants(winning_pos, som_nurons)
        # store the convolved value in the output (x,y)-
        # coordinate of the output image
        # output[y - pad, x - pad] = k
        # print(k)
        # print(roi)
#         output.append(winning_pos)

5
[[1 1 1 1 1]
 [1 1 1 1 1]
 [1 1 1 1 1]
 [1 1 1 1 1]
 [1 1 1 1 1]]
2


AttributeError: 'list' object has no attribute 'shape'

In [32]:
output

[(0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 (0, 0),
 

In [ ]:
(iH, iW) = image.shape[:2]
(kH, kW) = kernel.shape[:2]
# allocate memory for the output image, taking care to
# "pad" the borders of the input image so the spatial
# size (i.e., width and height) are not reduced
pad = (kW - 1) // 2
for y in np.arange(pad, iH + pad):
    for x in np.arange(pad, iW + pad):
        image = cv2.copyMakeBorder(image, pad, pad, pad, pad, cv2.BORDER_REPLICATE)
        roi = image[y, x]
        k = (roi * kernel).sum()
        print(roi)

In [14]:
som_y_size

NameError: name 'som_y_size' is not defined

In [39]:
x = [([  0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
         0,   0,  50,   0,   0,   0,   0, 237,   0,   0,   0,   0])]

In [41]:
test_som = create_train_som(x,n_features = 25)

5
Training...
 [ 100 / 100 ] 100% - 0:00:00 left 
 quantization error: 0.0
...ready!


In [260]:
som = MiniSom(5, 5, 25, sigma=0.3, learning_rate=0.5) # initialization of 6x6 SOM
som.random_weights_init(x)
print("Training...")
som.train_random(x, 100, verbose=True)

TypeError: 'int' object is not subscriptable

In [47]:
som.winner(x)

(0, 0)

In [164]:
image_list = x_train[0:100]

In [220]:
# Here we get the shape of the image and the kernal. We use this so we can set how
# the kernal slides across the image


# Here we add a buffer to thhe entire image so that when we get to the boarder we dont 
# lose any of the image



output = {}
image_index = 0

for image in image_list:

    
    (iH, iW) = image.shape[:2]
    (kH, kW) = kernel.shape[:2]
    pad = (kW - 1) // 2
    image = cv2.copyMakeBorder(image, pad, pad, pad, pad, cv2.BORDER_REPLICATE)
    
    # Here we actually slide the kernal across. The first for loop allows us to slide across
    # the height or each row as you will of the image, by the padding widthh
    for y in np.arange(pad, iH + pad):
        # This second for loop allows us to slide across the "columns" or te elements in that 
        # sepcific array 
        for x in np.arange(pad, iW + pad):
            # Now that we have the specific coordinants we're looking at on the image 
            # the height and width position (x,y) we can add the padding to get our patch
            roi = image[y - pad:y + pad + 1, x - pad:x + pad + 1]
            # Now, normally we would apply the kernal to our patch to augment the overall image
            # however we do not wish to do that. We are aiming to apply a SOM to this specific 
            # region of the image. 
            index = [y - pad,"-",x - pad]
            index = "".join(map(str,index))
            output.setdefault(index,[]).append(roi)
            
            
    image_index = image_index + 1






In [215]:
def create_train_som(x_train, n_features):
    
    # Create SOM dimensions
    som_nurons = int((math.sqrt(5*math.sqrt(n_features))))
#     print(som_nurons)
    x = som_nurons
    y = som_nurons
    
    #Create and train SOM
    som = MiniSom(x, y, n_features, sigma=0.3, learning_rate=0.5) # initialization of 6x6 SOM
    som.random_weights_init(x_train)
    print("Training...")
    som.train_random(x_train,100, verbose=False) # training with 100 iterations
    print("...ready!")
    return som

In [233]:
som_y_size = 25

labels = y_train[0:100]



som_results = {}

for key, value in output.items():
    
    
    print("processing patch ", key)
    # Here we have the kernal results for that specific region of each image. We convert to array and reshape so we can feed to SOM
    my_array = np.array(value)
    flat_array = flatten_and_reshape(my_array)
    
    # Using the data we now train our SOM on the specific region of the image
    som = create_train_som(flat_array, som_y_size)
    
    
    index_val = 0
    print("index value ", index_val)
    
    for x in flat_array:
        
        print("extracting winner for image ", index_val)
        winning_pos = som.winner(x)
#         print(winning_pos)
            # We now convert this coordinant into a numerical value so we can feed it to our next layer
        k = convert_coordinants(winning_pos, som_y_size)
            # store the convolved value in the output (x,y)-
            # coordinate of the output image
        print("winning value", k)
        image_key = [index_val, "-", key]
        image_key = "".join(map(str,image_key))
        print("saving to index", image_key)        
        som_results.setdefault(image_key,[]).append(k)
#         output[y - pad, x - pad] = k
    
        index_val = index_val + 1
        
    
    
    


processing patch  0-0
Training...
...ready!
index value  0
extracting winner for image  0
winning value 0
saving to index 0-0-0
extracting winner for image  1
winning value 0
saving to index 1-0-0
extracting winner for image  2
winning value 0
saving to index 2-0-0
extracting winner for image  3
winning value 0
saving to index 3-0-0
extracting winner for image  4
winning value 0
saving to index 4-0-0
extracting winner for image  5
winning value 0
saving to index 5-0-0
extracting winner for image  6
winning value 0
saving to index 6-0-0
extracting winner for image  7
winning value 0
saving to index 7-0-0
extracting winner for image  8
winning value 0
saving to index 8-0-0
extracting winner for image  9
winning value 0
saving to index 9-0-0
extracting winner for image  10
winning value 0
saving to index 10-0-0
extracting winner for image  11
winning value 0
saving to index 11-0-0
extracting winner for image  12
winning value 0
saving to index 12-0-0
extracting winner for image  13
winnin

winning value 0
saving to index 48-0-2
extracting winner for image  49
winning value 0
saving to index 49-0-2
extracting winner for image  50
winning value 0
saving to index 50-0-2
extracting winner for image  51
winning value 0
saving to index 51-0-2
extracting winner for image  52
winning value 0
saving to index 52-0-2
extracting winner for image  53
winning value 0
saving to index 53-0-2
extracting winner for image  54
winning value 0
saving to index 54-0-2
extracting winner for image  55
winning value 0
saving to index 55-0-2
extracting winner for image  56
winning value 0
saving to index 56-0-2
extracting winner for image  57
winning value 0
saving to index 57-0-2
extracting winner for image  58
winning value 0
saving to index 58-0-2
extracting winner for image  59
winning value 0
saving to index 59-0-2
extracting winner for image  60
winning value 0
saving to index 60-0-2
extracting winner for image  61
winning value 0
saving to index 61-0-2
extracting winner for image  62
winnin

saving to index 73-0-4
extracting winner for image  74
winning value 0
saving to index 74-0-4
extracting winner for image  75
winning value 0
saving to index 75-0-4
extracting winner for image  76
winning value 0
saving to index 76-0-4
extracting winner for image  77
winning value 0
saving to index 77-0-4
extracting winner for image  78
winning value 0
saving to index 78-0-4
extracting winner for image  79
winning value 0
saving to index 79-0-4
extracting winner for image  80
winning value 0
saving to index 80-0-4
extracting winner for image  81
winning value 0
saving to index 81-0-4
extracting winner for image  82
winning value 0
saving to index 82-0-4
extracting winner for image  83
winning value 0
saving to index 83-0-4
extracting winner for image  84
winning value 0
saving to index 84-0-4
extracting winner for image  85
winning value 0
saving to index 85-0-4
extracting winner for image  86
winning value 0
saving to index 86-0-4
extracting winner for image  87
winning value 0
saving

saving to index 60-0-6
extracting winner for image  61
winning value 0
saving to index 61-0-6
extracting winner for image  62
winning value 0
saving to index 62-0-6
extracting winner for image  63
winning value 0
saving to index 63-0-6
extracting winner for image  64
winning value 0
saving to index 64-0-6
extracting winner for image  65
winning value 0
saving to index 65-0-6
extracting winner for image  66
winning value 0
saving to index 66-0-6
extracting winner for image  67
winning value 0
saving to index 67-0-6
extracting winner for image  68
winning value 0
saving to index 68-0-6
extracting winner for image  69
winning value 0
saving to index 69-0-6
extracting winner for image  70
winning value 0
saving to index 70-0-6
extracting winner for image  71
winning value 0
saving to index 71-0-6
extracting winner for image  72
winning value 0
saving to index 72-0-6
extracting winner for image  73
winning value 0
saving to index 73-0-6
extracting winner for image  74
winning value 0
saving

extracting winner for image  75
winning value 0
saving to index 75-0-8
extracting winner for image  76
winning value 0
saving to index 76-0-8
extracting winner for image  77
winning value 0
saving to index 77-0-8
extracting winner for image  78
winning value 0
saving to index 78-0-8
extracting winner for image  79
winning value 0
saving to index 79-0-8
extracting winner for image  80
winning value 0
saving to index 80-0-8
extracting winner for image  81
winning value 0
saving to index 81-0-8
extracting winner for image  82
winning value 0
saving to index 82-0-8
extracting winner for image  83
winning value 0
saving to index 83-0-8
extracting winner for image  84
winning value 0
saving to index 84-0-8
extracting winner for image  85
winning value 0
saving to index 85-0-8
extracting winner for image  86
winning value 0
saving to index 86-0-8
extracting winner for image  87
winning value 0
saving to index 87-0-8
extracting winner for image  88
winning value 0
saving to index 88-0-8
extrac

...

saving to index 12-27-18
extracting winner for image  13
winning value 104
saving to index 13-27-18
extracting winner for image  14
winning value 104
saving to index 14-27-18
extracting winner for image  15
winning value 104
saving to index 15-27-18
extracting winner for image  16
winning value 104
saving to index 16-27-18
extracting winner for image  17
winning value 104
saving to index 17-27-18
extracting winner for image  18
winning value 104
saving to index 18-27-18
extracting winner for image  19
winning value 104
saving to index 19-27-18
extracting winner for image  20
winning value 104
saving to index 20-27-18
extracting winner for image  21
winning value 104
saving to index 21-27-18
extracting winner for image  22
winning value 104
saving to index 22-27-18
extracting winner for image  23
winning value 104
saving to index 23-27-18
extracting winner for image  24
winning value 104
saving to index 24-27-18
extracting winner for image  25
winning value 104
saving to index 25-27-18


extracting winner for image  31
winning value 54
saving to index 31-27-20
extracting winner for image  32
winning value 54
saving to index 32-27-20
extracting winner for image  33
winning value 54
saving to index 33-27-20
extracting winner for image  34
winning value 54
saving to index 34-27-20
extracting winner for image  35
winning value 54
saving to index 35-27-20
extracting winner for image  36
winning value 54
saving to index 36-27-20
extracting winner for image  37
winning value 54
saving to index 37-27-20
extracting winner for image  38
winning value 54
saving to index 38-27-20
extracting winner for image  39
winning value 54
saving to index 39-27-20
extracting winner for image  40
winning value 54
saving to index 40-27-20
extracting winner for image  41
winning value 54
saving to index 41-27-20
extracting winner for image  42
winning value 54
saving to index 42-27-20
extracting winner for image  43
winning value 54
saving to index 43-27-20
extracting winner for image  44
winnin

saving to index 21-27-22
extracting winner for image  22
winning value 4
saving to index 22-27-22
extracting winner for image  23
winning value 4
saving to index 23-27-22
extracting winner for image  24
winning value 4
saving to index 24-27-22
extracting winner for image  25
winning value 4
saving to index 25-27-22
extracting winner for image  26
winning value 4
saving to index 26-27-22
extracting winner for image  27
winning value 4
saving to index 27-27-22
extracting winner for image  28
winning value 4
saving to index 28-27-22
extracting winner for image  29
winning value 4
saving to index 29-27-22
extracting winner for image  30
winning value 4
saving to index 30-27-22
extracting winner for image  31
winning value 4
saving to index 31-27-22
extracting winner for image  32
winning value 4
saving to index 32-27-22
extracting winner for image  33
winning value 4
saving to index 33-27-22
extracting winner for image  34
winning value 4
saving to index 34-27-22
extracting winner for imag

saving to index 13-27-24
extracting winner for image  14
winning value 0
saving to index 14-27-24
extracting winner for image  15
winning value 0
saving to index 15-27-24
extracting winner for image  16
winning value 0
saving to index 16-27-24
extracting winner for image  17
winning value 0
saving to index 17-27-24
extracting winner for image  18
winning value 0
saving to index 18-27-24
extracting winner for image  19
winning value 0
saving to index 19-27-24
extracting winner for image  20
winning value 0
saving to index 20-27-24
extracting winner for image  21
winning value 0
saving to index 21-27-24
extracting winner for image  22
winning value 0
saving to index 22-27-24
extracting winner for image  23
winning value 0
saving to index 23-27-24
extracting winner for image  24
winning value 0
saving to index 24-27-24
extracting winner for image  25
winning value 0
saving to index 25-27-24
extracting winner for image  26
winning value 0
saving to index 26-27-24
extracting winner for imag

...ready!
index value  0
extracting winner for image  0
winning value 0
saving to index 0-27-26
extracting winner for image  1
winning value 0
saving to index 1-27-26
extracting winner for image  2
winning value 0
saving to index 2-27-26
extracting winner for image  3
winning value 0
saving to index 3-27-26
extracting winner for image  4
winning value 0
saving to index 4-27-26
extracting winner for image  5
winning value 0
saving to index 5-27-26
extracting winner for image  6
winning value 0
saving to index 6-27-26
extracting winner for image  7
winning value 0
saving to index 7-27-26
extracting winner for image  8
winning value 0
saving to index 8-27-26
extracting winner for image  9
winning value 0
saving to index 9-27-26
extracting winner for image  10
winning value 0
saving to index 10-27-26
extracting winner for image  11
winning value 0
saving to index 11-27-26
extracting winner for image  12
winning value 0
saving to index 12-27-26
extracting winner for image  13
winning value 

output2

So the issue is we now have the output results for each of the trained SOM's YAY! What we need to do however is we need to somehow convert that back into an image of sorts. So we need to construct that sampling layer for eachh image. The problem is that the data is indexed on the patch not the image. The only thing I have really is the index in the dictionary 

we can create a nested dictionary, and loop through everythihng, referefcing the image we want to create but i feel like that is a overly labours way surely there is some sort of paralasation that we can do where I can do this in paralell insead of looping thorough everythhing 



In [256]:
def filter_dict(d, filter_string):
    for key, val in d.items():
        values = key.split("-")
        image_index = values[0]
        if filter_string != image_index:
            continue
        yield key, val

In [259]:
for key, val in filter_dict(som_results, "1"):
#     print(key)
    values = key.split("-")
    image_index = values[0]
#     print(image_index)
    y = int(values[1])
    x = int(values[2])
    output[y - pad, x - pad] = val
    

1-0-0
1-0-1
1-0-2
1-0-3
1-0-4
1-0-5
1-0-6
1-0-7
1-0-8
1-0-9
1-0-10
1-0-11
1-0-12
1-0-13
1-0-14
1-0-15
1-0-16
1-0-17
1-0-18
1-0-19
1-0-20
1-0-21
1-0-22
1-0-23
1-0-24
1-0-25
1-0-26
1-0-27
1-1-0
1-1-1
1-1-2
1-1-3
1-1-4
1-1-5
1-1-6
1-1-7
1-1-8
1-1-9
1-1-10
1-1-11
1-1-12
1-1-13
1-1-14
1-1-15
1-1-16
1-1-17
1-1-18
1-1-19
1-1-20
1-1-21
1-1-22
1-1-23
1-1-24
1-1-25
1-1-26
1-1-27
1-2-0
1-2-1
1-2-2
1-2-3
1-2-4
1-2-5
1-2-6
1-2-7
1-2-8
1-2-9
1-2-10
1-2-11
1-2-12
1-2-13
1-2-14
1-2-15
1-2-16
1-2-17
1-2-18
1-2-19
1-2-20
1-2-21
1-2-22
1-2-23
1-2-24
1-2-25
1-2-26
1-2-27
1-3-0
1-3-1
1-3-2
1-3-3
1-3-4
1-3-5
1-3-6
1-3-7
1-3-8
1-3-9
1-3-10
1-3-11
1-3-12
1-3-13
1-3-14
1-3-15
1-3-16
1-3-17
1-3-18
1-3-19
1-3-20
1-3-21
1-3-22
1-3-23
1-3-24
1-3-25
1-3-26
1-3-27
1-4-0
1-4-1
1-4-2
1-4-3
1-4-4
1-4-5
1-4-6
1-4-7
1-4-8
1-4-9
1-4-10
1-4-11
1-4-12
1-4-13
1-4-14
1-4-15
1-4-16
1-4-17
1-4-18
1-4-19
1-4-20
1-4-21
1-4-22
1-4-23
1-4-24
1-4-25
1-4-26
1-4-27
1-5-0
1-5-1
1-5-2
1-5-3
1-5-4
1-5-5
1-5-6
1-5-7
1-5-8
1-5-9
1-5-10
1-5

In [239]:
for key, value in som_results.items():
#     print(key)
    values = key.split("-")
    image_index = values[0]
    patch_y_coord = values[1]
    patch_x_coord = values[2]
    
    output = np.zeros((iH, iW), dtype="float32")
    output[y - pad, x - pad] = k
    
    

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46

95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41

73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19

63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9

28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
7

...

67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13

65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11

48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
9

46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
8

44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
8